## Data quality analysis for table `default_product_info`

This table contains basic information of the products, these information are repeated over all the other tables. Let's use this table to represent a product-offer, that means, the minimum to represent the intuition and split other dimensions linking to it.

We can start by checking the schema.

In [0]:
%python
import pyspark.sql.functions as F
from pyspark.sql.functions import (
    col,
    count,
    countDistinct,
    desc,
    isnan,
    avg,
    min as spark_min,
    max as spark_max,
    expr,
    percentile_approx,
    trim,
    split,
    split_part,
    lower
)
import plotly.express as px
import plotly.graph_objects as go

In [0]:
%sql
DESCRIBE mvp.bronze_feeds.default_product_info

col_name data_type comment aw_deep_link string The unique Awin tracking link for the product. product_name string The full title or name of the product. aw_product_id bigint Awin's unique internal identifier for the product. merchant_product_id string The unique ID assigned to the product by the merchant. merchant_image_url string Direct URL to the product image on the merchant's server. description string Detailed description of the product features. merchant_category string The category name assigned by the merchant. search_price double The current selling price used for search filtering.

The data types look ok, there is no categorical fields, just fields with *identifiers* like  `aw_product_id` and `merchant_product_id`, and fields that are expected to contain different information like *urls*, *textual descriptions*, and *names*.

The first approach to check is the number of null values in each of the fields.

In [0]:
%python
import pandas as pd

# Load data
df = spark.table("mvp.bronze_feeds.default_product_info")

# Get schema
schema = df.schema
total_count = df.count()

# Prepare summary stats
summary = {}
for field in schema:
    col_name = field.name
    col_type = field.dataType.typeName()
    col_stats = {}
    # Null count
    if col_type == 'double':
        null_count = df.filter(
            col(col_name).isNull() | isnan(col(col_name))
        ).count()
    else:
        null_count = df.filter(
            col(col_name).isNull()
        ).count()
    col_stats['null_count'] = null_count
    # Distinct count
    distinct_count = df.select(col_name).distinct().count()
    col_stats['distinct_count'] = distinct_count
    # Percent nulls
    col_stats['null_pct_total'] = null_count / total_count if total_count else 0
    col_stats['null_pct_distinct'] = null_count / distinct_count if distinct_count else 0
    if col_type == 'double':
        stats = df.select(
            spark_max(col(col_name)).alias('max'),
            spark_min(col(col_name)).alias('min'),
            avg(col(col_name)).alias('avg'),
            percentile_approx(col(col_name), 0.5).alias('median')
        ).collect()[0]
        col_stats.update({
            'max': stats['max'],
            'min': stats['min'],
            'avg': stats['avg'],
            'median': stats['median']
        })
    elif col_type == 'string':
        if col_name in ['product_name', 'merchant_category']:
            top_values = df.groupBy(col_name).count().orderBy(desc("count")).limit(100).toPandas()
            col_stats['top_values'] = top_values
    summary[col_name] = col_stats

In [0]:
# Charts for double columns
double_cols = [f.name for f in schema if f.dataType.typeName() == 'double']
double_stats = {k: v for k, v in summary.items() if k in double_cols}
if double_stats:
    double_df = pd.DataFrame(double_stats).T
    fig1 = px.bar(
        double_df[['max', 'min', 'avg', 'median']],
        barmode='group',
        color_discrete_sequence=px.colors.sequential.Viridis
    )
    fig1.update_layout(title="Double Columns: Max, Min, Avg, Median")
    fig1.show()

In [0]:
# Charts for product_name, merchant_category, aw_product_id, and merchant_product_id
for col_name in ['product_name', 'merchant_category', 'aw_product_id', 'merchant_product_id']:
    if col_name in summary and 'top_values' in summary[col_name]:
        top_values = summary[col_name]['top_values']
    else:
        # For aw_product_id and merchant_product_id, get top 100 most frequent values
        top_values = df.groupBy(col_name).count().orderBy(desc("count")).limit(100).toPandas()
    if not top_values.empty:
        fig2 = px.bar(
            top_values,
            x=col_name,
            y='count',
            color='count',
            color_continuous_scale='viridis'
        )
        fig2.update_layout(title=f"Top 100 Most Common Values for {col_name}")
        fig2.show()

Interesting observations:

* there are products with the same `product_name`, on the other hand, only a few `merchant_product_id` repeats, that means, and `aw_product_id` don't repeat. That means:
  * `aw_product_id` is a real id for the products in Awin system.
  * `merchant_product_id` is not directly related to the product name, there may be products with same name but varing in color, size, pattern etc and they are not seen as the same in the merchant system, that means.

* `merchant_categories` follow different patterns, some of them are just the category name, other follow a hierarchy pattern like `Moda Feminina > Roupas > Saias`, there is a need to clean it.

In [0]:
# Null count and percent chart
null_stats = []
for k, v in summary.items():
    null_stats.append({
        'column': k,
        'null_count': v['null_count'],
        'null_pct_total': v['null_pct_total'],
        'null_pct_distinct': v['null_pct_distinct']
    })
null_df = pd.DataFrame(null_stats)
fig3 = px.bar(
    null_df,
    x='column',
    y='null_count',
    color='null_count',
    color_continuous_scale='viridis',
    hover_data=['null_pct_total', 'null_pct_distinct']
)
fig3.update_layout(title="Null Value Count and Percent per Column")
fig3.show()

Multiple elements has no `description` or `merchant_category` what may be a problem for our problem, as we would use these fields to enrich our AI platform. Let's keep an eye on them, first, checking the percentage of elements with null values for these columns.

In [0]:
cols_to_plot = ['description', 'merchant_category', 'merchant_image_url']
pie_data = []
for col_name in cols_to_plot:
    null_count = df.filter(col(col_name).isNull()).count()
    not_null_count = df.count() - null_count
    pie_data.append({
        'column': col_name,
        'labels': ['Null', 'Not Null'],
        'values': [null_count, not_null_count]
    })

for data in pie_data:
    fig = px.pie(
        names=data['labels'],
        values=data['values'],
        title=f"Percentual de nulos para {data['column']}"
    )
    fig.show()

The percentage for null `description` is relevant, meaning, removing these rows would result in removing a big part of our dataset. On the other hand, removing those with `merchant_cathegory` null would impact et all as this is less then 2% of the data. For `merchant_image_url` it's less than 0.1%, then it could be easily removed.

I will keep thoose with null `description`, but remove those with null `merchant_category` or null `merchant_image_url`.

In [0]:
default_product_info_bronze = spark.table("mvp.bronze_feeds.default_product_info")
default_product_info_silver = default_product_info_bronze.where(col("merchant_category").isNotNull() & col("merchant_image_url").isNotNull())

We also need to clean the `merchant_category`, for this, I will take the last segment when splitted by `>`, that is, a category like `Moda Feminina > Roupas > Saias` becomes only `Saias`, I will also normalize the string by removing leading and trailing whitespaces and transforming to lowercase.

In [0]:
category = F.split_part(F.col("merchant_category"), F.lit(">"), F.lit(-1))
default_product_info_silver = default_product_info_silver.withColumn("category", lower(trim(category)))

In [0]:
display(default_product_info_silver.where(F.col("merchant_category").contains(">")).limit(10))

aw_deep_link product_name aw_product_id merchant_product_id merchant_image_url description merchant_category search_price category https://www.awin1.com/pclick.php?p=33888086911&a=999127&m=32675 PUMA PUMA Boné Essentials – Cor Branco 33888086911 4056204300794 https://images.puma.net/images/052919/10/fnd/BRA/ Este modelo de boné esportivo de seis painéis ganha uma nova versão street-chic com linhas elegantes e elementos de marca em destaque. DETALHES Boné com seis painéis Ilhós bordado Fecho de contato de tecido na parte traseira Logo PUMA bordado em 3D na parte frontal Vestuário e acessórios > Acessórios para roupas > Chapéus 79.9 chapéus https://www.awin1.com/pclick.php?p=33888086909&a=999127&m=32675 PUMA PUMA Boné Essentials – Cor Azul 33888086909 4056204301074 https://images.puma.net/images/052919/18/fnd/BRA/ Este modelo de boné esportivo de seis painéis ganha uma nova versão street-chic com linhas elegantes e elementos de marca em destaque. DETALHES Boné com seis painéis Ilhós bordado Fecho de contato de tecido na parte traseira Logo PUMA bordado em 3D na parte frontal Vestuário e acessórios > Acessórios para roupas > Chapéus 79.9 chapéus https://www.awin1.com/pclick.php?p=33888086907&a=999127&m=32675 PUMA PUMA Boné Essentials – Cor Preto 33888086907 4056204301142 https://images.puma.net/images/052919/09/fnd/BRA/ Este modelo de boné esportivo de seis painéis ganha uma nova versão street-chic com linhas elegantes e elementos de marca em destaque. DETALHES Boné com seis painéis Ilhós bordado Fecho de contato de tecido na parte traseira Logo PUMA bordado em 3D na parte frontal Vestuário e acessórios > Acessórios para roupas > Chapéus 79.9 chapéus https://www.awin1.com/pclick.php?p=33888086917&a=999127&m=32675 PUMA PUMA Boné PUMA Metal Cat – Cor Preto 33888086917 4056207606916 https://images.puma.net/images/021269/01/fnd/BRA/ Versátil e funcional, o boné PUMA Metal Cat traz aba curva e tira de ajuste com fechamento hook-and-loop em uma variedade de cores. DETALHES Aba curva Faixa de transpiração feita em tecido de alta absorção para maior conforto e desempenho Tira de ajuste com fechamento hook-and-loop Ilhós bordados 100% Poliéster Vestuário e acessórios > Acessórios para roupas > Chapéus 109.9 chapéus https://www.awin1.com/pclick.php?p=33888086915&a=999127&m=32675 PUMA PUMA Boné PUMA Metal Cat – Cor Azul 33888086915 4059504716395 https://images.puma.net/images/021269/07/fnd/BRA/ Versátil e funcional, o boné PUMA Metal Cat traz aba curva e tira de ajuste com fechamento hook-and-loop em uma variedade de cores. DETALHES Aba curva Faixa de transpiração feita em tecido de alta absorção para maior conforto e desempenho Tira de ajuste com fechamento hook-and-loop Ilhós bordados 100% Poliéster Vestuário e acessórios > Acessórios para roupas > Chapéus 109.9 chapéus https://www.awin1.com/pclick.php?p=33888095911&a=999127&m=32675 PUMA PUMA Boné Ess Juvenil – Cor Branco – Juv 33888095911 4059504723607 https://images.puma.net/images/021688/03/fnd/BRA/ Feito em material 100% algodão, o boné PUMA Essentials traz tira de ajuste com fechamento hook-and-loop para o encaixe perfeito. Com logo PUMA bordado à frente em efeito 3D, o modelo foi feito para a proteção e diversão dos pequenos. DETALHES Modelagem ajustável Tira de ajuste em tecido com fechamento hook-and-loop Logo PUMA em efeito 3D bordado à frente 100% Algodão Vestuário e acessórios > Acessórios para roupas > Chapéus 59.9 chapéus https://www.awin1.com/pclick.php?p=33887967901&a=999127&m=32675 PUMA PUMA Tênis PUMA Cali Feminino – Cor Branco 33887967901 4060978971203 https://images.puma.net/images/369155/04/sv01/fnd/BRA/ Inspirado no street style dos anos 80, o tênis PUMA Cali traz cabedal em resistente perfurado, linhas clássicas e entressola grossa com impressão texturizada para entregar a combinação ideal entre conforto e design. DETALHES Cabedal em material resistente Sola e entressola de borracha Fechamento de cadarço para o ajuste ideal Branding PUMA na língua e nas laterais Faix

Vamos estudar o mapeamento das classes entre `merchant_category`e `category`:

In [0]:
# Agrupa e seleciona os top 5 category
top_categories = (
    default_product_info_silver.groupBy("category")
    .count()
    .orderBy(desc("count"))
    .limit(5)
    .select("category")
    .toPandas()["category"]
    .tolist()
)

# Filtra apenas os top 5 category
df_top = default_product_info_silver.filter(col("category").isin(top_categories))

# Agrupa por category e merchant_category e conta as linhas
sankey_df = (
    df_top.groupBy("category", "merchant_category")
    .count()
    .toPandas()
)

# Prepara os nodes e links para o Sankey
categories = sankey_df["category"].unique().tolist()
merchant_categories = sankey_df["merchant_category"].unique().tolist()
nodes = categories + merchant_categories

node_indices = {name: i for i, name in enumerate(nodes)}
sankey_df["source"] = sankey_df["category"].map(node_indices)
sankey_df["target"] = sankey_df["merchant_category"].map(node_indices)

# Sankey plot
fig = go.Figure(data=[go.Sankey(
    node=dict(
        pad=30,
        thickness=20,
        line=dict(color="rgba(0,0,0,0.2)", width=0.5),
        label=nodes,
        color=["#636EFA"]*len(categories) + ["#00CC96"]*len(merchant_categories)
    ),
    link=dict(
        source=sankey_df["source"],
        target=sankey_df["target"],
        value=sankey_df["count"],
        color="rgba(100,100,100,0.3)"
    )
)])

fig.update_layout(
    title_text="Sankey: category x merchant_category (Top 5 category)",
    font_size=12,
    plot_bgcolor='rgba(0,0,0,0)',
    paper_bgcolor='rgba(0,0,0,0)',
    autosize=True,
    margin=dict(l=0, r=0, t=0, b=0),
    height=1400,
    width=1000
)
fig.update_layout(
    dragmode='zoom',
    hovermode='x unified'
)
fig.show()

In the previous graph we can see multiple categories were merged into one, let's review the distribution of category values.

In [0]:
# Tabela dos diferentes valores de category e suas contagens
category_counts_df = (
    default_product_info_silver.groupBy("category")
    .count()
    .orderBy(desc("count"))
)
display(category_counts_df)

# Gráfico de barras dos valores de category
category_counts_pd = category_counts_df.limit(50).toPandas()
fig = px.bar(
    category_counts_pd,
    x="category",
    y="count",
    color="count",
    color_continuous_scale="viridis",
    title="Distribuição dos valores de category (Top 50)"
)
fig.update_layout(xaxis_tickangle=-45)
fig.show()

category count tênis 108441 top manga curta 107788 roupas 72909 blusas 65794 sandália 58079 calça 54753 vestido 42433 tênis performance 38366 shorts/bermuda 34344 bota 31462 chinelo 24606 calças 20408 rasteira 18760 top regata 17342 conjunto curto 16967 camisa 14856 sapatilha 14663 outros 12693 shorts 12052 scarpin 11846 bermudas 11246 vestidos 10918 calcinha 10756 camiseta polo 10310 jaqueta 9901 moletom 9475 top manga longa 8406 cueca 8312 pijama 8226 sutiã 8146 saia 7285 bolsa 7167 over top 6505 meia 6075 saias 5830 camiseta 5736 sapato social 5268 sapato casual 5112 óculos 5075 mocassim/oxford 4955 conjunto lingerie 4693 conjunto longo 4112 sapatos 4064 casacos 3575 boné 3545 calcinhas 3338 conjunto biquíni 3250 cinto 3115 camisetas e tops 2867 mochila 2779 cama 2738 maiô 2704 casual 2595 meias 2528 top biquíni 2481 sandálias 2459 beachwear 2446 top curto 2362 sutiãs 2260 chuteira 2222 pijamas 2178 chinelos 1971 relógio 1969 shorts/saia 1961 camisetas e polos 1929 bermuda 1906 carteira 1810 conjuntos 1809 perfume 1781 underwear 1778 camisa de time 1755 calcinha biquíni 1640 cardiga/sueter 1580 rasteirinhas 1569 camisetas 1495 corrida 1452 ropa y accesorios 1452 chinelos e sandálias 1442 mala/mochila/necessaire 1406 saída de praia 1331 cuecas 1321 sapato 1316 body 1256 macacões 1164 camiseta regata 1124 shorts/bermuda boardshorts 1115 macacão 1077 botas 1068 cabelos 1031 sunga 988 bolsas 972 calça legging 938 jaqueta e blusa de frio 892 calça moletom 883 banho 879 perfumes femininos 864 maternidade/modeladora 808 relógios 765 top 755 short 718 biquínis 637 legging 635 bermudas e shorts 624 futsal 610 escolar 570 base 553 tops 545 maiôs 544 perfumes masculinos 541 sapatilhas 536 são paulo 515 tamancos 510 fitness e musculação 501 sungas 460 palmeiras 451 society 450 casacos e jaquetas 441 regatas e tops 435 cintos 429 bolsas e mochilas 420 uniformes de futebol 417 vasco da gama 407 campo 389 chuteiras 355 bodies 348 jaquetas e moletons 343 mochilas 338 gloss 318 camisas 311 acessórios 291 flamengo 286 basquete 275 corinthians 274 tratamento 272 corpo e banho 270 grêmio 255 chapéus 249 maquiagem 249 conjunto 249 calção 240 artigos esportivos 239 fluminense 224 santos 224 escolares 216 caminhada 211 corretivo 210 calças & leggings 204 atlético mineiro 195 jaquetas & moletons 187 internacional 185 bonés e gorros 181 cruzeiro 178 pó facial 178 blush 176 botafogo 165 calções 163 louças 163 goiás 162 blusas de proteção 161 eletroportáteis para cozinha 159 camiseta manga longa 159 natação 155 beisebol 149 batom 144 saias e leggings 141 jardineira 141 bolsas & mochilas 136 luvas 132 acessórios de cabelo 131 hidratantes 126 malas 126 meiões 121 máscara de cílios 117 calçados 117 skate 116 lápis 112 manchester city 112 cintas e modeladores 108 brincos 107 snkrs 107 bola 101 shampoo 94 óculos de natação 92 térmicos e compressão 91 roupas de cama 90 meião 87 cachecol/lenço/luva 86 real madrid 85 chinelos & sandálias 83 utilidades domésticas 82 chapéu/gorro 80 boné/chapéu/gorro 78 saídas de praia 77 kit uniforme de futebol 75 goleiros 73 acessórios para servir 73 mesa 66 pantufas 66 short-saia 65 bahia 64 finalizadores 62 artigos de futebol 62 suplementos 61 unhas 61 cropped 59 óculos de sol 58 garrafa 58 camisa polo 57 athletico paranaense 57 condicionador 56 trilha e trekking 54 masculino 54 automobilismo 54 barcelona 54 futebol americano 53 calção de time 53 sport recife 53 produtos de futebol 52 acessórios para cozinha 52 mala 51 sabonetes 51 potes de armazenamento 51 vôlei 50 bolas 50 iluminador 50 conjuntos de roupas 49 juventus 47 caneleira 47 copos de água e suco 45 nordeste 43 cama e banho 43 demaquilante 42 saias & vestidos & macacões 41 organização de banheiro 41 guardanapos 40 paris saint-germain 40 porta temperos 39 organização de closets 39 cuidados labiais 38 máscaras faciais 38 sampaio corrêa 37 bonés & viseiras 37 patins 37 organização de cozinha 37 jogo americano 36 brasil 35 mala/necessaire 35 bola de futebol 34 atléti

Now, let's evaluate the `search_price`, we already checked that the type is `double`, meaning the data type is correct, also, let's check the median, maximum and minimum values. If we have negative of null values, that means we have an error.

In [0]:
# Calculate absolute min and max
min_val = default_product_info_silver.agg(F.min("search_price")).first()[0]
max_val = default_product_info_silver.agg(F.max("search_price")).first()[0]

# Calculate quartiles using approxQuantile
q1, median, q3 = default_product_info_silver.approxQuantile("search_price", [0.25, 0.5, 0.75], 0.01)

# Count records in each quartile
quartile_counts = [
    default_product_info_silver.filter(F.col("search_price") <= q1).count(),
    default_product_info_silver.filter((F.col("search_price") > q1) & (F.col("search_price") <= median)).count(),
    default_product_info_silver.filter((F.col("search_price") > median) & (F.col("search_price") <= q3)).count(),
    default_product_info_silver.filter(F.col("search_price") > q3).count()
]

# Create summary table
summary_data = [
    ("Minimum", min_val, None),
    ("Q1 (25%)", q1, quartile_counts[0]),
    ("Median (50%)", median, quartile_counts[1]),
    ("Q3 (75%)", q3, quartile_counts[2]),
    ("Maximum", max_val, quartile_counts[3])
]

summary_df = spark.createDataFrame(summary_data, ["Statistic", "Value", "Record_Count"])
display(summary_df)

Statistic Value Record_Count Minimum 1.0 null Q1 (25%) 79.99 288925 Median (50%) 139.9 261702 Q3 (75%) 229.99 254904 Maximum 8495.0 272464

The minimum value is 1, what is strange, let's get the distribution of values between the minimum and the first quartile.

In [0]:
# Filter values in the first quartile
first_quartile_df = default_product_info_silver.filter(F.col("search_price") <= q1)

# Convert to Pandas for plotting
first_quartile_pd = first_quartile_df.select("search_price").toPandas()

# Plot histogram
fig = px.histogram(
    first_quartile_pd,
    x="search_price",
    nbins=50,
    title="Distribution of search_price in the First Quartile (<= Q1)"
)
fig.update_layout(xaxis_title="search_price", yaxis_title="Count")
fig.show()

In [0]:
# Filter values in the second quartile
second_quartile_df = default_product_info_silver.filter((F.col("search_price") > q1) & (F.col("search_price") <= median))

# Convert to Pandas for plotting
second_quartile_pd = second_quartile_df.select("search_price").toPandas()

# Plot histogram
fig = px.histogram(
    second_quartile_pd,
    x="search_price",
    nbins=50,
    title="Distribution of search_price in the Second Quartile (Q1 < search_price <= Median)"
)
fig.update_layout(xaxis_title="search_price", yaxis_title="Count")
fig.show()

In [0]:
# Filter values in the third quartile
third_quartile_df = default_product_info_silver.filter((F.col("search_price") > median) & (F.col("search_price") <= q3))

# Convert to Pandas for plotting
third_quartile_pd = third_quartile_df.select("search_price").toPandas()

# Plot histogram
fig = px.histogram(
    third_quartile_pd,
    x="search_price",
    nbins=50,
    title="Distribution of search_price in the Third Quartile (Median < search_price <= Q3)"
)
fig.update_layout(xaxis_title="search_price", yaxis_title="Count")
fig.show()

In [0]:
# Filter values in the fourth quartile
fourth_quartile_df = default_product_info_silver.filter(F.col("search_price") > q3)

# Convert to Pandas for plotting
fourth_quartile_pd = fourth_quartile_df.select("search_price").toPandas()

# Plot histogram
fig = px.histogram(
    fourth_quartile_pd,
    x="search_price",
    nbins=50,
    title="Distribution of search_price in the Fourth Quartile (search_price > Q3)"
)
fig.update_layout(xaxis_title="search_price", yaxis_title="Count")
fig.show()

In general, for the price, there are some outliers, they are more relevant in the end segment intead of the first. From the data perspective, it it not enought to tell it's wrong, but maximum and minimum is not enought to describe the `search_price`column as it varies a lot. Later, in bronze, we can take care of that in different categories, then we will understand if the problem is related to category or not.

We can remove some fields that could be obtained from other sources, here we will keep only the minimum necessary to identify a product offer and it's category (in this table we are still missing the merchant, but using the `merchant_product_id` we can recover it later from other table in bronze).

This is the expected transformation to map `default_product_info` from bronze to silver:

In [0]:
default_product_info_bronze = spark.table("mvp.bronze_feeds.default_product_info")
default_product_info_silver = default_product_info_bronze.where(F.col("merchant_category").isNotNull() & F.col("merchant_image_url").isNotNull())

category = F.split_part(F.col("merchant_category"), F.lit(">"), F.lit(-1))
default_product_info_silver = default_product_info_silver.withColumn("category", F.lower(F.trim(category)))

kept_columns = [
    "aw_product_id",
    "merchant_product_id",
    "category",

    "product_name",    
    "description",
        
    "aw_deep_link",
    "search_price"
]

default_product_info_silver = default_product_info_silver.select(*kept_columns)

display(default_product_info_silver.limit(10))

aw_product_id merchant_product_id category product_name description aw_deep_link search_price 42424777485 2R739APF02DDX-19374 conjunto lingerie Sutiã Sem Alças 2Rios 81906 Taça B Sutiã Sem Alças 2Rios 81906 Taça B Sutiã confeccionado em microfibra, proporcionando leveza e conforto. Modelagem tomara que caia e base com espuma para maior segurança. Busto com bojo e aro, modela e valoriza os seios. Decote em formato V e pequeno laço de cetim central dão charme à peça. Laterais largas e com parte interna em silicone garante melhor aderência. Alças removíveis e reguláveis. Composição: 92% Poliamida e 08% Elastano. Forro do bojo: 100% Poliéster. TABELA DE MEDIDAS: TAMANHO: P - MANEQUIM: 40 - BUSTO(cm): 78-85 - TÓRAX(cm): 67-74 TAMANHO: M - MANEQUIM: 42 - BUSTO(cm): 86-92 - TÓRAX(cm): 75-81 TAMANHO: G - MANEQUIM: 44 - BUSTO(cm): 93-98 - TÓRAX(cm): 82-87 TAMANHO: GG - MANEQUIM: 46 - BUSTO(cm): 99-104 - TÓRAX(cm): 88-93 https://www.awin1.com/pclick.php?p=42424777485&a=999127&m=17697 137.48 42424777486 2R739APF02DDX-19375 conjunto lingerie Sutiã Sem Alças 2Rios 81906 Taça B Sutiã Sem Alças 2Rios 81906 Taça B Sutiã confeccionado em microfibra, proporcionando leveza e conforto. Modelagem tomara que caia e base com espuma para maior segurança. Busto com bojo e aro, modela e valoriza os seios. Decote em formato V e pequeno laço de cetim central dão charme à peça. Laterais largas e com parte interna em silicone garante melhor aderência. Alças removíveis e reguláveis. Composição: 92% Poliamida e 08% Elastano. Forro do bojo: 100% Poliéster. TABELA DE MEDIDAS: TAMANHO: P - MANEQUIM: 40 - BUSTO(cm): 78-85 - TÓRAX(cm): 67-74 TAMANHO: M - MANEQUIM: 42 - BUSTO(cm): 86-92 - TÓRAX(cm): 75-81 TAMANHO: G - MANEQUIM: 44 - BUSTO(cm): 93-98 - TÓRAX(cm): 82-87 TAMANHO: GG - MANEQUIM: 46 - BUSTO(cm): 99-104 - TÓRAX(cm): 88-93 https://www.awin1.com/pclick.php?p=42424777486&a=999127&m=17697 137.48 42424777487 2R739APF02DDX-19376 conjunto lingerie Sutiã Sem Alças 2Rios 81906 Taça B Sutiã Sem Alças 2Rios 81906 Taça B Sutiã confeccionado em microfibra, proporcionando leveza e conforto. Modelagem tomara que caia e base com espuma para maior segurança. Busto com bojo e aro, modela e valoriza os seios. Decote em formato V e pequeno laço de cetim central dão charme à peça. Laterais largas e com parte interna em silicone garante melhor aderência. Alças removíveis e reguláveis. Composição: 92% Poliamida e 08% Elastano. Forro do bojo: 100% Poliéster. TABELA DE MEDIDAS: TAMANHO: P - MANEQUIM: 40 - BUSTO(cm): 78-85 - TÓRAX(cm): 67-74 TAMANHO: M - MANEQUIM: 42 - BUSTO(cm): 86-92 - TÓRAX(cm): 75-81 TAMANHO: G - MANEQUIM: 44 - BUSTO(cm): 93-98 - TÓRAX(cm): 82-87 TAMANHO: GG - MANEQUIM: 46 - BUSTO(cm): 99-104 - TÓRAX(cm): 88-93 https://www.awin1.com/pclick.php?p=42424777487&a=999127&m=17697 137.48 42424777488 2R739APF02DDX-19377 conjunto lingerie Sutiã Sem Alças 2Rios 81906 Taça B Sutiã Sem Alças 2Rios 81906 Taça B Sutiã confeccionado em microfibra, proporcionando leveza e conforto. Modelagem tomara que caia e base com espuma para maior segurança. Busto com bojo e aro, modela e valoriza os seios. Decote em formato V e pequeno laço de cetim central dão charme à peça. Laterais largas e com parte interna em silicone garante melhor aderência. Alças removíveis e reguláveis. Composição: 92% Poliamida e 08% Elastano. Forro do bojo: 100% Poliéster. TABELA DE MEDIDAS: TAMANHO: P - MANEQUIM: 40 - BUSTO(cm): 78-85 - TÓRAX(cm): 67-74 TAMANHO: M - MANEQUIM: 42 - BUSTO(cm): 86-92 - TÓRAX(cm): 75-81 TAMANHO: G - MANEQUIM: 44 - BUSTO(cm): 93-98 - TÓRAX(cm): 82-87 TAMANHO: GG - MANEQUIM: 46 - BUSTO(cm): 99-104 - TÓRAX(cm): 88-93 https://www.awin1.com/pclick.php?p=42424777488&a=999127&m=17697 137.48 42424777489 2R739APF04EIP-19374 conjunto lingerie Sutiã Tomara Que Caia 2Rios 81906 Taça B Sutiã Tomara Que Caia 2Rios 81906 Taça B Sutiã confeccionado em microfibra, proporcionando leveza e conforto. Modelagem tomara que caia e base com espuma para maior segurança. Busto com bojo e aro, modela e 

Let's do this transformation as a task `default_product_info_silver` after the task `default_product_info_bronze`.